In [2]:
import pandas as pd
import numpy as np
import simpy
import random

In [31]:
connect = pd.read_excel(r'data/connect2.xlsx')
dist1 = pd.read_excel(r'data/dist2.xlsx')
location = pd.read_excel(r'data/location2.xlsx')

In [3]:
a=[1,2]
print(a.pop(0))
a

1


[2]

In [4]:
service_num = 0
global_var = 0
class ChargingStation:
    def __init__(self, env, station_id,latitude, longitude,battery_num,service_time,charge_time,min_num):
        self.env = env
        self.station_id = station_id
        self.battery_num = battery_num
        self.latitude = latitude
        self.longitude = longitude
        self.service_time = service_time
        self.charge_time = charge_time
        self.min_num = min_num
        self.busy = False
        self.queue = []
        


    def charge(self):
        yield self.env.timeout(np.random.exponential(scale=self.charge_time))
        self.battery_num+=2
        print(f" Station {self.station_id} Charge at {self.env.now} have battery {self.battery_num} ")


        
    def serve(self,uav):
        global global_var
        print(f"serve function {uav.uav_id},station{self.station_id}, queue length :{len(self.queue)}")
        uav.ifcharge = True
        print(f"serve function {uav.uav_id},charge status :{uav.ifcharge}")
        if len(self.queue)>0 and self.battery_num>self.min_num:
            self.busy = True
            yield self.env.timeout(np.random.exponential(scale=self.service_time))
            if len(self.queue)>0: 
                uav1 = self.queue[0]
                self.queue.pop(0).ifcharge = False
                self.battery_num-=2
                print(f"UAV {uav1.uav_id} at time {self.env.now} at {self.station_id} charge battery left {self.battery_num}")
                self.env.process(self.charge())
                print(f"after serving UAV {uav1.uav_id},charge status :{uav1.ifcharge}")
                print("-------------------")
            global_var += 1
            self.busy = False
        if len(self.queue)>0 and self.battery_num>self.min_num:
            self.env.process(self.serve(self.queue[0]))
            


In [5]:
class Truck:
    def __init__(self, env, truck_id,latitude, longitude,speed,order=0,iffree = True):
        self.env = env
        self.truck_id = truck_id
        self.latitude = latitude
        self.longitude = longitude
        self.busy = False
        self.speed = speed
        self.order = order
        self.iffree  =iffree
        self.target = 0

In [ ]:
class Distribution_center:
    def __init__(self, env, station_id,latitude, longitude,battery_num,service_time,charge_time,min_num):
        self.env = env
        self.station_id = station_id
        self.battery_num = battery_num
        self.latitude = latitude
        self.longitude = longitude
        self.truck_num = 1
        self.trucklist = [Truck(env,i+station_id,latitude,longitude,32) for i in range(self.truck_num)]
        self.charge_time = char
        self.uavqueue = []
        

In [ ]:
class Order:
    def __init__(self, env, demand_point_id,uav_id,order_id,servicetime,beigin_time,end_time,direc,distance,if_finished = False):
        self.env = env
        self.demand_point_id = demand_point_id
        self.uav_id = uav_id
        self.order_id = order_id
        self.begin_time = beigin_time
        self.end_time = end_time
        self.servicetime = servicetime
        self.direc = direc
        self.distance = distance
        self.if_finished = if_finished

In [40]:
finished_order = []
chargelist  = []
finished_num = 0
class Service_point:
    def __init__(self, env, demand_point_id,arrival_time,latitude, longitude,serviceid,servicetime):
        self.env = env
        self.demand_point_id = demand_point_id
        self.arrival_time = arrival_time
        self.latitude = latitude
        self.longitude = longitude
        self.serviceid = serviceid
        self.servicetime = servicetime


class UAV:
    def __init__(self, env, uav_id,latitude, longitude,speed,order=0,iffree = True,ifcharge = False):
        self.env = env
        self.uav_id = uav_id
        self.latitude = latitude
        self.longitude = longitude
        self.busy = False
        self.speed = speed
        self.order = order
        self.iffree  =iffree
        self.ifcharge  =ifcharge
        self.target = 0
        
        
        
    def fulfill_demand(self,order):
        global finished_order
        global finished_num
        global chargelist
        for i in range(location.shape[0]):
            chargelist.append(ChargingStation(self.env,i,location.iloc[i,2],location.iloc[i,3],10,0.1,5,2))
        while True:
            self.order = order
            dist = self.order.distance
            direc = self.order.direc
            self.iffree = False
            while self.target!=len(direc):
                if self.ifcharge==False:
                    yield self.env.timeout(dist[self.target] / self.speed)
                    print(f"UAV{self.uav_id}  arrive at point {direc[self.target]} at time {self.env.now}, target:{self.target}")
                    chargelist[direc[self.target]].queue.append(self)
                    #self.ifcharge=True
                    self.env.process(chargelist[direc[self.target]].serve(self))
                    self.target+=1
            #print(f"Demand of{self.order.begin_time} / {self.order.order_id} finished at time {self.env.now}")
            if self.target==len(direc):
                finished_order.append(order)
                finished_num+=1
                break

In [41]:
total_orders_generated=0
total_order = []
class Demand_point:
    total_orders_generated = 0  # 类变量用于跟踪所有需求点的需求数量

    def __init__(self, env, demand_point_id, latitude, longitude, uavnum, demand_time):
        self.env = env
        self.demand_point_id = demand_point_id
        self.latitude = latitude
        self.longitude = longitude
        self.uavnum = uavnum
        self.uavqueue = []
        self.demand_time = demand_time
        self.orders_generated = 0

    def generate_demand(self):
        global total_orders_generated
        global total_order
        while True:
            order_id = random.randint(1, 10000)
            self.orders_generated += 1  # 增加订单数量计数器
            total_orders_generated+=1
            direc = [4,5,0]
            distance = [500,530,430]
            neworder = Order(self.env, self.demand_point_id,0,order_id,0,self.env.now,0,direc,distance)
            total_order.append(neworder)
            if(self.uavnum>0):
                uav = self.uavqueue.pop(0)
                self.uavnum-=1
                self.env.process(uav.fulfill_demand(neworder))
            #print(f"Demand generated at point {self.demand_point_id} at time {self.env.now}")
            yield self.env.timeout(np.random.exponential(scale=self.demand_time))

In [12]:
import simpy
import numpy as np
import random
import pandas as pd

connect = pd.read_excel(r'data/connect2.xlsx')
dist1 = pd.read_excel(r'data/dist2.xlsx')
location = pd.read_excel(r'data/location2.xlsx')
service_point_number = 249

service_num = 0
global_var = 0


class ChargingStation:
    def __init__(self, env, station_id, latitude, longitude, battery_num, service_time, charge_time, min_num):
        self.env = env
        self.station_id = station_id
        self.battery_num = battery_num
        self.latitude = latitude
        self.longitude = longitude
        self.service_time = service_time
        self.charge_time = charge_time
        self.min_num = min_num
        self.busy = False
        self.queue = []
        self.service_num = 400

    def charge(self):
        yield self.env.timeout(np.random.exponential(scale=self.charge_time))
        self.battery_num += 2
        print(f" Station {self.station_id} Charge at {self.env.now} have battery {self.battery_num} ")
        

    def servetime(self):
        yield self.env.timeout(0.1)

    def servetime2(self):
        if len(self.queue) < self.service_num:
            yield self.env.timeout(0.15)
        else:
            while len(self.queue) >= self.service_num:
                yield self.env.timeout(0.5)

    def serve(self, uav):
        global global_var
        print(f"serve function {uav.uav_id},station{self.station_id}, queue length :{len(self.queue)}")
        uav.ifcharge = True
        continue_serve = True
        while self.battery_num < self.min_num:
            yield self.env.process(self.charge())
        while continue_serve and uav.ifcharge != False:
            if len(self.queue) > 0 and self.battery_num > self.min_num:
                self.busy = True
                print(f"Try to service serve function {uav.uav_id},time {self.env.now}")
                if len(self.queue) > 0 and self.battery_num > self.min_num:
                    if self.station_id == service_point_number:
                        yield self.env.process(self.servetime2())
                    else:
                        yield self.env.process(self.servetime())
                    uav1 = self.queue[0]
                    self.queue.pop(0).ifcharge = False
                    print(f"After Go service serve function {uav1.uav_id},time {self.env.now}")
                    self.battery_num -= 2
                    print(
                        f"UAV {uav1.uav_id} at time {self.env.now} at {self.station_id} charge battery left {self.battery_num}")
                    self.env.process(self.charge())
                    global_var += 1
                    self.busy = False
                    if uav1.uav_id == uav.uav_id:
                        continue_serve = False  # 设置标志为 False，退出循环
                        #yield self.env.timeout(0)
                    else:
                        if len(self.queue) > 0 and self.battery_num > self.min_num:
                            self.env.process(self.serve(self.queue[0]))
                        else:
                            pass


class Order:
    def __init__(self, env, demand_point_id, uav_id, order_id, servicetime, beigin_time, end_time, direc, distance,
                 if_finished=False):
        self.env = env
        self.demand_point_id = demand_point_id
        self.uav_id = uav_id
        self.order_id = order_id
        self.begin_time = beigin_time
        self.end_time = end_time
        self.servicetime = servicetime
        self.direc = direc
        self.distance = distance
        self.if_finished = if_finished


finished_order = []
service_timelist = []
chargelist = []
finished_num = 0
uav_cost = 0


class Service_point:
    def __init__(self, env, demand_point_id, arrival_time, latitude, longitude, serviceid, servicetime):
        self.env = env
        self.demand_point_id = demand_point_id
        self.arrival_time = arrival_time
        self.latitude = latitude
        self.longitude = longitude
        self.serviceid = serviceid
        self.servicetime = servicetime


class UAV:
    def __init__(self, env, uav_id, latitude, longitude, speed, order=0, iffree=True, ifcharge=False):
        self.env = env
        self.uav_id = uav_id
        self.latitude = latitude
        self.longitude = longitude
        self.busy = False
        self.speed = speed
        self.order = order
        self.iffree = iffree
        self.ifcharge = ifcharge
        self.target = 0
        self.start_time = 0
        self.end_time = 0

    def fulfill_demand(self, order):
        global finished_order
        global finished_num
        global chargelist
        global service_timelist
        for i in range(location.shape[0]):
            chargelist.append(ChargingStation(self.env, i, location.iloc[i, 2], location.iloc[i, 3], 5, 2, 2, 2))
        while True:
            self.order = order
            dist = self.order.distance
            direc = self.order.direc
            self.start_time = self.env.now
            self.iffree = False
            while self.target != len(direc):
                if self.ifcharge == False:
                    yield self.env.timeout(dist[self.target] / self.speed)
                    print(
                        f"UAV{self.uav_id}  arrive at point {direc[self.target]} at time {self.env.now}, target:{self.target}")
                    chargelist[direc[self.target]].queue.append(self)
                    # self.ifcharge=True
                    yield self.env.process(chargelist[direc[self.target]].serve(self))
                    #yield self.env.timeout(0)
                    self.target += 1
            # print(f"Demand of{self.order.begin_time} / {self.order.order_id} finished at time {self.env.now}")
            if self.target == len(direc):
                finished_order.append(order)
                finished_num += 1
                self.iffree = True
                self.end_time = self.env.now
                service_timelist.append(self.end_time - self.start_time)
                break


total_orders_generated = 0
total_order = []


class Demand_point:
    total_orders_generated = 0  # 类变量用于跟踪所有需求点的需求数量

    def __init__(self, env, demand_point_id, latitude, longitude, uavnum, demand_time):
        self.env = env
        self.demand_point_id = demand_point_id
        self.latitude = latitude
        self.longitude = longitude
        self.uavnum = uavnum
        self.uavqueue = []
        self.demand_time = demand_time
        self.orders_generated = 0

    def waitnewuav(self):
        while self.uavnum <= 0:
            print("Wait for new UAV")
            yield self.env.timeout(5)

    def generate_demand(self):
        global total_orders_generated
        global total_order
        while True:
            order_id = random.randint(1, 10000)
            self.orders_generated += 1  # 增加订单数量计数器
            total_orders_generated += 1
            direc = [18, 69, 180, 210, 249, 217, 72, 66, 0]
            distance = [dist1.iloc[0, 18], dist1.iloc[18, 69], dist1.iloc[69, 180], dist1.iloc[180, 210],
                        dist1.iloc[210, 249], dist1.iloc[249, 217], dist1.iloc[217, 72], dist1.iloc[72, 66],
                        dist1.iloc[66, 0]]
            neworder = Order(self.env, self.demand_point_id, 0, order_id, 0, self.env.now, 0, direc, distance)
            total_order.append(neworder)
            if self.uavnum > 0:
                uav = self.uavqueue.pop(0)
                self.uavnum -= 1
                self.env.process(uav.fulfill_demand(neworder))
                yield self.env.timeout(0)
                self.uavqueue.append(uav)
                neworder.if_finished = True
                neworder.end_time = self.env.now
            else:
                self.env.process(self.waitnewuav())
            # print(f"Demand generated at point {self.demand_point_id} at time {self.env.now}")
            yield self.env.timeout(np.random.exponential(scale=self.demand_time))


def run_simulation(num_demand_points, latitude, longitude, uavnum, demand_time, simulation_time):
    # 创建仿真环境
    env = simpy.Environment()
    # 创建需求点并添加到仿真环境中
    demand_points = []
    for i in range(num_demand_points):
        demand_point = Demand_point(env, demand_point_id=i, latitude=latitude, longitude=longitude, uavnum=uavnum,
                                    demand_time=demand_time)

        used_ids = set()  # 存储已使用的uav_id
        for i in range(demand_point.uavnum):
            uavid = random.randint(1, 50000)
            while uavid in used_ids:  # 检查uavid是否已存在于集合中
                uavid = random.randint(1, 50000)
            used_ids.add(uavid)  # 将uavid添加到集合中
            demand_point.uavqueue.append(
                UAV(env, uav_id=uavid, latitude=demand_point.latitude, longitude=demand_point.longitude,
                    speed=random.randint(30, 50)))

        demand_points.append(demand_point)
        env.process(demand_point.generate_demand())
    # 运行仿真直到指定时间
    env.run(until=simulation_time)
    return demand_points


# 调用函数来运行仿真
num_demand_points = 4
latitude = 37.7749
longitude = -122.4194
uavnum = 300
demand_time = 0.1
simulation_time = 24

demand_points = run_simulation(num_demand_points, latitude, longitude, uavnum, demand_time, simulation_time)

UAV32644  arrive at point 18 at time 0.15339535357846415, target:0
serve function 32644,station18, queue length :1
Try to service serve function 32644,time 0.15339535357846415
UAV21280  arrive at point 18 at time 0.15339535357846415, target:0
serve function 21280,station18, queue length :2
Try to service serve function 21280,time 0.15339535357846415
UAV33073  arrive at point 18 at time 0.15339535357846415, target:0
serve function 33073,station18, queue length :3
Try to service serve function 33073,time 0.15339535357846415
UAV11986  arrive at point 18 at time 0.1731075746695524, target:0
serve function 11986,station18, queue length :4
Try to service serve function 11986,time 0.1731075746695524
UAV3876  arrive at point 18 at time 0.17584345410214183, target:0
serve function 3876,station18, queue length :5
Try to service serve function 3876,time 0.17584345410214183
UAV46276  arrive at point 18 at time 0.1886075779490025, target:0
serve function 46276,station18, queue length :6
Try to serv

KeyboardInterrupt: 

In [6]:
if 0.1%0.05==0:
    print("1")

1


In [31]:
connect = pd.read_excel(r'data/connect2.xlsx')
dist1 = pd.read_excel(r'data/dist2.xlsx')
location = pd.read_excel(r'data/location2.xlsx')
location

Unnamed: 0  index         lng        lat
0             0      0  113.962367  22.590502
1             1      1  113.552982  22.357572
2             2      2  113.080259  22.600326
3             3      3  113.386631  23.054778
4             4      4  114.073908  22.537692
..          ...    ...         ...        ...
245         245    254  113.394703  22.083607
246         246    255  113.345705  22.129363
247         247    256  113.346690  22.139801
248         248    257  113.372497  22.063397
249         249    258  113.280000  22.580000

[250 rows x 4 columns]

In [124]:
import simpy
import numpy as np
import random
import pandas as pd

connect = pd.read_excel(r'data/connect2.xlsx')
dist1 = pd.read_excel(r'data/dist2.xlsx')
location = pd.read_excel(r'data/location2.xlsx')
service_point_number = 249

service_num = 0
global_var = 0


class ChargingStation:
    def __init__(self, env, station_id, latitude, longitude, battery_num, service_time, charge_time, min_num):
        self.env = env
        self.station_id = station_id
        self.battery_num = battery_num
        self.latitude = latitude
        self.longitude = longitude
        self.service_time = service_time
        self.charge_time = charge_time
        self.min_num = min_num
        self.busy = False
        self.queue = []
        self.service_num = 400

    def charge(self):
        yield self.env.timeout(np.random.exponential(scale=self.charge_time))
        self.battery_num += 2
        print(f" Station {self.station_id} Charge at {self.env.now} have battery {self.battery_num} ")
        

    def servetime(self):
        yield self.env.timeout(np.random.exponential(scale=self.service_time))

    def servetime2(self):
        if len(self.queue) < self.service_num:
            yield self.env.timeout(np.random.exponential(scale=self.service_time)+np.random.exponential(scale=0.017))
        else:
            while len(self.queue) >= self.service_num:
                yield self.env.timeout(0.001)
                
    def servetime2(self):
        yield self.env.timeout(np.random.exponential(scale=self.service_time)+np.random.exponential(scale=0.017))

    def serve(self, uav):
        global global_var
        print(f"serve function {uav.uav_id},station{self.station_id}, queue length :{len(self.queue)}")
        uav.ifcharge = True
        continue_serve = True
        while self.queue[0].uav_id != uav.uav_id:
            yield self.env.timeout(0.001)
        while self.battery_num < self.min_num:
            yield self.env.process(self.charge())
        while continue_serve and uav.ifcharge != False:
            if len(self.queue) > 0 and self.battery_num >= self.min_num and self.queue[0].uav_id == uav.uav_id:
                self.busy = True
                print(f"Try to service serve function {uav.uav_id},time {self.env.now}")
                for i in uavlist:
                    i.service_time = self.env.now - i.start_time
                queuelist[self.station_id].append(len(self.queue))
                if len(self.queue) > 0 and self.battery_num >= self.min_num:
                    if self.queue[0].uav_id==uav.uav_id:
                        if self.station_id == service_point_number:
                            yield self.env.process(self.servetime2())
                        else:
                            yield self.env.process(self.servetime())
                    else:
                        yield self.env.process(self.servetime())
                    uav1 = self.queue[0]
                    self.queue.pop(0).ifcharge = False
                    uav1.ifcharge = False
                    print(f"After Go service serve function {uav1.uav_id},time {self.env.now}")
                    self.battery_num -= 2
                    print(
                        f"UAV {uav1.uav_id} at time {self.env.now} at {self.station_id} charge battery left {self.battery_num}")
                    self.env.process(self.charge())
                    global_var += 1
                    self.busy = False
                    if uav1.uav_id == uav.uav_id:
                        print("now")
                        continue_serve = False  # 设置标志为 False，退出循环
                        break
                    else:
                        if len(self.queue) > 0 and self.battery_num > self.min_num:
                            print("continue")
                            self.env.process(self.serve(self.queue[0]))
                        else:
                            pass
                if self.battery_num < self.min_num:
                    yield self.env.process(self.charge())


class Order:
    def __init__(self, env, demand_point_id, uav_id, order_id, servicetime, beigin_time, end_time, direc, distance,
                 if_finished=False):
        self.env = env
        self.demand_point_id = demand_point_id
        self.uav_id = uav_id
        self.order_id = order_id
        self.begin_time = beigin_time
        self.end_time = end_time
        self.servicetime = servicetime
        self.direc = direc
        self.distance = distance
        self.if_finished = if_finished


finished_order = []
service_timelist = []
chargelist = []
finished_num = 0
uav_cost = 0
latitudelist = [[]]



class Service_point:
    def __init__(self, env, demand_point_id, arrival_time, latitude, longitude, serviceid, servicetime):
        self.env = env
        self.demand_point_id = demand_point_id
        self.arrival_time = arrival_time
        self.latitude = latitude
        self.longitude = longitude
        self.serviceid = serviceid
        self.servicetime = servicetime


class UAV:
    def __init__(self, env, uav_id, latitude, longitude, speed, order=0, iffree=True, ifcharge=False):
        self.env = env
        self.uav_id = uav_id
        self.latitude = latitude
        self.longitude = longitude
        self.busy = False
        self.speed = speed
        self.order = order
        self.iffree = iffree
        self.ifcharge = ifcharge
        self.target = 0
        self.start_time = 0
        self.end_time = 0
        self.service_time = 0

    def fulfill_demand(self, order):
        global finished_order
        global finished_num
        global chargelist
        global service_timelist
        for i in range(location.shape[0]):
            chargelist.append(ChargingStation(self.env, i, location.iloc[i, 2], location.iloc[i, 3], 5000, 0.0027, 2, 2))
        while True:
            self.order = order
            dist = self.order.distance
            direc = self.order.direc
            self.start_time = self.env.now
            self.service_time = 0
            self.iffree = False
            while self.target != len(direc):
                if self.ifcharge == False:
                    if self.target < len(direc):
                        yield self.env.timeout(dist[self.target] / self.speed)
                        print(
                            f"UAV{self.uav_id}  arrive at point {direc[self.target]} at time {self.env.now}, target:{self.target}")
                        chargelist[direc[self.target]].queue.append(self)
                        # self.ifcharge=True
                        yield self.env.process(chargelist[direc[self.target]].serve(self))
                        yield self.env.timeout(0)
                        self.target += 1
            # print(f"Demand of{self.order.begin_time} / {self.order.order_id} finished at time {self.env.now}")
            if self.target == len(direc):
                finished_order.append(order)
                finished_num += 1
                for uav1 in uavlist:
                    if uav1.target == len(uav1.order.direc):
                        finisheduavlist.append(uav1)
                        uavlist.remove(uav1)
                        uav1.order.if_finished = True
                        uav1.order.end_time = self.env.now
                        demand_points[uav1.order.direc[-1]].uavqueue.append(uav1)
                        demand_points[uav1.order.direc[-1]].uavnum+=1
                self.iffree = True
                self.end_time = self.env.now
                service_timelist.append(self.end_time - self.start_time)
                break



total_orders_generated = 0
total_order = []
unassigned_order = []
assigned_order = []
uavlist = []
finisheduavlist = []
queuelist = []
for i in range(location.shape[0]):
    queuelist.append([])


class Demand_point:
    total_orders_generated = 0  # 类变量用于跟踪所有需求点的需求数量

    def __init__(self, env, demand_point_id, latitude, longitude, uavnum, demand_time):
        self.env = env
        self.demand_point_id = demand_point_id
        self.latitude = latitude
        self.longitude = longitude
        self.uavnum = uavnum
        self.uavqueue = []
        self.demand_time = demand_time
        self.orders_generated = 0

    def waitnewuav(self):
        while self.uavnum <= 0:
            print("Wait for new UAV")
            for uav1 in uavlist:
                if uav1.target == len(uav1.order.direc):
                    finisheduavlist.append(uav1)
                    uavlist.remove(uav1)
                    uav1.order.if_finished = True
                    uav1.order.end_time = self.env.now
                    if uav1.order.direc[-1]==self.demand_point_id:
                        self.uavqueue.append(uav1)
                        self.uavnum+=1
            yield self.env.timeout(0.1)

    def generate_demand(self):
        global total_orders_generated
        global total_order
        global unassigned_order
        global assigned_order
        global uavlist
        global queuelist
        while True:
            order_id = random.randint(1, 10000)
            self.orders_generated += 1  # 增加订单数量计数器
            total_orders_generated += 1
            #direc = [18, 69, 180, 210, 249, 217, 72, 66, 0]
            direc = [[15,69,177,175,217,249,213,176,181,72,22,18,10,0],[209,230,249,211,1],[200,249,215,204,202,197,199,201,192,2],[154,249,97,3]]
            distance = []
            for i in range(len(direc)):
                distance1 = []
                for j in range(len(direc[i])):
                    if j==0:
                        distance1.append(dist1.iloc[i,direc[i][j]])
                    else:
                        distance1.append(dist1.iloc[direc[i][j-1],direc[i][j]])
                distance.append(distance1) 
            neworder = Order(self.env, self.demand_point_id, 0, order_id, 0, self.env.now, 0, direc[self.demand_point_id], distance[self.demand_point_id])
            total_order.append(neworder)
            unassigned_order.append(neworder)
            if self.uavnum > 0 and len(unassigned_order)<2:
                uav = self.uavqueue.pop(0)
                uavlist.append(uav)
                self.uavnum -= 1
                unassigned_order.pop(0)
                assigned_order.append(neworder)
                self.env.process(uav.fulfill_demand(neworder))
                yield self.env.timeout(0)
            if self.uavnum > 0 and len(unassigned_order)>=2:
                uav = self.uavqueue.pop(0)
                uavlist.append(uav)
                self.uavnum -= 1
                neworder1 = unassigned_order.pop(0)
                assigned_order.append(neworder1)
                self.env.process(uav.fulfill_demand(neworder1))
                yield self.env.timeout(0)
                
            # if self.uavnum<=0:
            #     for uav1 in uavlist:
            #         if uav1.target == len(uav1.order.direc):
            #             finisheduavlist.append(uav1)
            #             uavlist.remove(uav1)
            #             uav1.order.if_finished = True
            #             uav1.order.end_time = self.env.now
            #             if uav1.order.direc[-1]==self.demand_point_id:
            #                 self.uavqueue.append(uav1)
            #                 self.uavnum+=1
            #     pass
            # else:
            #     self.env.process(self.waitnewuav())
            # print(f"Demand generated at point {self.demand_point_id} at time {self.env.now}")
            yield self.env.timeout(np.random.exponential(scale=self.demand_time))


def run_simulation(num_demand_points, uavnum, demand_time, simulation_time):
    # 创建仿真环境
    env = simpy.Environment()
    # 创建需求点并添加到仿真环境中
    demand_points = []
    for i in range(num_demand_points):
        # demand_point = Demand_point(env, demand_point_id=i, latitude=latitude, longitude=longitude, uavnum=uavnum,
        #                             demand_time=demand_time)
        demand_point = Demand_point(env, demand_point_id=i, latitude=location.iloc[i,2], longitude=location.iloc[i,3], uavnum=uavnum,
                                    demand_time=demand_time)
        used_ids = set()  # 存储已使用的uav_id
        for i in range(demand_point.uavnum):
            uavid = random.randint(1, 50000000)
            while uavid in used_ids:  # 检查uavid是否已存在于集合中
                uavid = random.randint(1, 5000000)
            used_ids.add(uavid)  # 将uavid添加到集合中
            demand_point.uavqueue.append(
                UAV(env, uav_id=uavid, latitude=demand_point.latitude, longitude=demand_point.longitude,
                    speed=random.randint(30, 40)))
        demand_points.append(demand_point)
        env.process(demand_point.generate_demand())
    # 运行仿真直到指定时间
    env.run(until=simulation_time)
    return demand_points


# 调用函数来运行仿真
num_demand_points = 4
uavnum = 6000
demand_time = 0.004
simulation_time = 5
demand_points = run_simulation(num_demand_points,  uavnum, demand_time, simulation_time)

UAV9376270  arrive at point 209 at time 0.16873113689679525, target:0
serve function 9376270,station209, queue length :1
Try to service serve function 9376270,time 0.16873113689679525
After Go service serve function 9376270,time 0.1694693491435141
UAV 9376270 at time 0.1694693491435141 at 209 charge battery left 4998
now
UAV37815641  arrive at point 209 at time 0.1793478210584222, target:0
serve function 37815641,station209, queue length :1
Try to service serve function 37815641,time 0.1793478210584222
After Go service serve function 37815641,time 0.18190046686441463
UAV 37815641 at time 0.18190046686441463 at 209 charge battery left 4996
now
UAV44660565  arrive at point 209 at time 0.1967304273999156, target:0
serve function 44660565,station209, queue length :1
Try to service serve function 44660565,time 0.1967304273999156
After Go service serve function 44660565,time 0.19710396731353413
UAV 44660565 at time 0.19710396731353413 at 209 charge battery left 4994
now
UAV38594694  arrive a

In [125]:
print(len(total_order))

print(len(finisheduavlist))
print(finished_num)

4927
199
199


In [126]:
for i in finisheduavlist:
    print(i.service_time)

1.197469766486707
1.2344268676568366
1.2398428688940744
1.286023995954456
1.2722203514467092
1.3174825135389792
1.3852534565035752
1.4151186681725694
1.3878804126918776
1.3188059992011727
1.5178814482945562
1.5117584291321449
1.4196350916363616
1.5430014875221822
1.516595925873608
1.4713740246946698
1.56488298275812
1.4488716632303051
1.6204085746601937
1.5514469966728306
1.4640254305087166
1.5382175277558747
1.5097441702775818
1.5658830458274045
1.691813766846995
1.8182226170635467
1.8124696781034868
1.6924874312292915
1.7876775293653626
1.8601526859627624
1.7536692300687653
1.9879266044047177
1.86596780274448
1.8345040677754576
1.9038026075688241
1.8437219059322756
1.8721141715793557
2.0080448276859073
2.2014252981154927
2.142530176851945
2.056669638551574
2.0037398185206103
2.0920414296903167
2.003397148672224
1.9646610525498156
2.0623803726651624
2.0121223535251813
2.146764943499707
2.218067290094848
2.2412826067686074
2.1538546955021682
2.0708945260511085
2.089108185973336
2.11023

In [127]:
for i in uavlist:
    print(i.service_time)

4.998433017787548
4.9967459713980515
4.996248196443224
4.994016740538617
4.990943072725511
4.987338973020123
4.977555410965739
4.970907526900923
4.96623254388941
4.966025715381775
4.9607977992029495
4.960095703503064
4.960084049825473
4.958623201461418
4.9577204232315575
4.955871276565257
4.955094128005169
4.954511629825201
4.952197705007791
4.9511369520484845
4.946591952072056
4.94617045115661
4.943499107036013
4.941536427910086
4.940801359113439
4.939865102430009
4.938205920990153
4.935610575290798
4.935434499938786
4.931455937126497
4.926725921924908
4.924077505689438
4.920065186309085
4.915770362328571
4.913711901167259
4.9074885522983145
4.906798650965471
4.904849306836026
4.901707867952619
4.900068777424738
4.899812862072966
4.895453773773059
4.8926607998792315
4.892637682704719
4.886219188201948
4.882430950299926
4.878232751732867
4.877904877091584
4.875829336019941
4.8716223072761995
4.871353417394651
4.869380092263613
4.867114104273437
4.8612399945147775
4.858631882487254
4.85

In [128]:
print(len(assigned_order))

4927


In [129]:
print(len(unassigned_order))

0


In [108]:
finished_num

65

In [130]:
indexlist = []
averagelist = []
for i in range(len(queuelist)):
    if len(queuelist[i])!=0:
        indexlist.append(i)
        averagelist.append(sum(queuelist[i])/len(queuelist[i]))

In [131]:
import pandas as pd
aq = pd.DataFrame()
aq['location'] = indexlist
aq['queuelength'] = averagelist
aq

location  queuelength
0          1     1.000000
1          2     1.000000
2          3     1.000000
3         15     3.252025
4         69     3.557034
5         97     1.000000
6        154     2.886861
7        175     3.445061
8        177     2.998921
9        192     1.014286
10       197     1.021429
11       199     1.000000
12       200     2.893379
13       201     1.035714
14       202     1.013605
15       204     1.000000
16       209     3.679775
17       211     1.000000
18       215     1.006667
19       217     3.347826
20       230     3.634615
21       249  1426.846154

In [117]:
import pandas as pd
aq = pd.DataFrame()
aq['location'] = indexlist
aq['queuelength'] = averagelist
aq.to_excel(r'queuelenth1.xlsx')